# Symbolic ODE solutions for mkin

Johannes Ranke, 11 May 2020

This [jupyter](https://jupyter.org/) notebook was created using [Maxima-Jupyter](https://github.com/robert-dodier/maxima-jupyter) which makes it comfortable to write and execute code for the [Maxima](http://maxima.sourceforge.net) Computer Algebra System (CAS). It was prepared to support the implementation of symbolic solutions for some of the systems of linear autonomous differential equations used in the [mkin](https://pkgdown.jrwb.de/mkin) R package. In particular, parent compounds that degrade with Simple First-Order (SFO) or Dual First-Order in Parallel (DFOP) kinetics, coupled to one SFO metabolite are now implemented in mkin. More solutions would be possible, expecially for systems that can be represented by coefficient matrices like the Single First-Order Reversible Binding (SFORB) equations and their combinations with SFO equations. In order to explore this, Maxima code is shown here that solves the corresponding initial value problem for the SFORB-SFO system as an example. However, this solution is not implemented in mkin at current.

The solutions that are implemented (SFO-SFO and DFOP-SFO) were obtained using the [desolve](http://maxima.sourceforge.net/docs/manual/maxima_21.html#IDX817) function as shown below.

## Preliminaries

The following two functions for setting up matrices used to solve the initial value problem for autonomous systems (without time on the right hand side) are from a first [wonderful blog entry](https://themaximalist.org/2017/02/27/extracting-matrices-from-the-output-of-eigenvalues) by Eric Barth.

In [1]:
eigU(v):=transpose(apply('matrix,makelist(part(v,2,i,1),i,1,length(part(v,2)),1)))$
eigdiag(v):=apply('diag_matrix,part(v,1,1))$

The following function for solving systems of linear equations in matrix form is from [another wonderful blog entry](https://themaximalist.org/2017/02/28/solving-the-matrix-vector-equation-axb-in-maxima/).

In [2]:
matsolve(A,b):=block(
   [AugU],
   AugU:echelon(addcol(A,b)),
   backsolve(AugU)
 )$

backsolve(augU):=block(
 [i,j,m,n,b,x,klist,k,np,nosoln:false],
 [m,n]:matsize(augU),
 b:col(augU,n),
 klist:makelist(concat('%k,i),i,1,n-1),
 k:0,
 x:transpose(matrix(klist)),
 for i:m thru 1 step -1 do (
   np:pivot(row(augU,i)), 
   if is(equal(np,n)) then
     (nosoln:true,return())
   else if not(is(equal(np,0))) then
     (x[np]:b[i],
     for j:np+1 thru n-1 do
       x[np]:x[np]-augU[i,j]*x[j])
    ),
 if nosoln then 
    return([])
 else 
   return(expand(x)) 
)$

matsize(A):=[length(A),length(transpose(A))]$

pivot(rr):=block([i,rlen],
 p:0,
 rlen:length(transpose(rr)),
 for i:1 thru rlen do( 
 if is(equal(part(rr,1,i),1)) then (p:i,return())), 
 return(p)
)$

## SFO-SFO with complete formation

In [3]:
diff_1_sfo: 'diff(n1(t), t) = - k1  * n1(t);
diff_2_sfo_sfo: 'diff(n2(t), t) = k1 * n1(t) - k2 * n2(t);

                            d
(%o7)                       -- (n1(t)) = - k1 n1(t)
                            dt

                       d
(%o8)                  -- (n2(t)) = k1 n1(t) - k2 n2(t)
                       dt

In [4]:
atvalue(n1(t), t = 0, n10)$
atvalue(n2(t), t = 0, n20)$
sol_sfo_sfo: desolve([diff_1_sfo, diff_2_sfo_sfo], [n1(t), n2(t)])$
sol_sfo_sfo[1];
sol_sfo_sfo[2];

                                           - k1 t
(%o12)                       n1(t) = n10 %e

                                             - k2 t            - k1 t
                  ((k2 - k1) n20 - k1 n10) %e         k1 n10 %e
(%o13)    n2(t) = --------------------------------- + ---------------
                               k2 - k1                    k2 - k1

## SFO-SFO with formation fraction

In [5]:
diff_2_sfo_f12_sfo: 'diff(n2(t), t) = f12 * k1 * n1(t) - k2 * n2(t);

                     d
(%o14)               -- (n2(t)) = f12 k1 n1(t) - k2 n2(t)
                     dt

In [6]:
atvalue(n1(t), t = 0, n10)$
atvalue(n2(t), t = 0, n20)$
sol_sfo_f12_sfo: desolve([diff_1_sfo, diff_2_sfo_f12_sfo], [n1(t), n2(t)])$
sol_sfo_f12_sfo[1];
sol_sfo_f12_sfo[2];

                                           - k1 t
(%o18)                       n1(t) = n10 %e

                                              - k2 t                - k1 t
               ((k2 - k1) n20 - f12 k1 n10) %e         f12 k1 n10 %e
(%o19) n2(t) = ------------------------------------- + -------------------
                              k2 - k1                        k2 - k1

## SFO-SFO without formation fraction

In [7]:
diff_1_sfo_k120_sfo: 'diff(n1(t), t) = - (k10 + k12)  * n1(t);
diff_2_sfo_k120_sfo: 'diff(n2(t), t) = k12 * n1(t) - k2 * n2(t);

                      d
(%o20)                -- (n1(t)) = ((- k12) - k10) n1(t)
                      dt

                       d
(%o21)                 -- (n2(t)) = k12 n1(t) - k2 n2(t)
                       dt

In [8]:
atvalue(n1(t), t = 0, n10)$
atvalue(n2(t), t = 0, n20)$
sol_sfo_k120_sfo: desolve([diff_1_sfo_k120_sfo, diff_2_sfo_k120_sfo], [n1(t), n2(t)])$
sol_sfo_k120_sfo[1];
sol_sfo_k120_sfo[2];

                                       - (k12 + k10) t
(%o25)                   n1(t) = n10 %e

                                                  - k2 t
               ((k2 - k12 - k10) n20 - k12 n10) %e
(%o26) n2(t) = -----------------------------------------
                            k2 - k12 - k10
                                                                - (k12 + k10) t
                                                      k12 n10 %e
                                                    + -------------------------
                                                           k2 - k12 - k10

## DFOP-SFO with complete formation

In [9]:
diff_11_dfop: 'diff(m1(t), t) = - l1 * m1(t);
diff_12_dfop: 'diff(m2(t), t) = - l2 * m2(t);
diff_2_dfop_sfo: 'diff(n2(t), t) = l1 * m1(t) + l2 * m2(t) - k2 * n2(t);

                            d
(%o27)                      -- (m1(t)) = - l1 m1(t)
                            dt

                            d
(%o28)                      -- (m2(t)) = - l2 m2(t)
                            dt

                d
(%o29)          -- (n2(t)) = (- k2 n2(t)) + l2 m2(t) + l1 m1(t)
                dt

In [10]:
atvalue(m1(t), t = 0, g * n10)$
atvalue(m2(t), t = 0, (1 - g) * n10)$
atvalue(n2(t), t = 0, n20)$
sol_dfop_sfo: desolve([diff_11_dfop, diff_12_dfop, diff_2_dfop_sfo], [m1(t), m2(t), n2(t)])$
sol_dfop_sfo[1];
sol_dfop_sfo[2];
mapped_sol_dfop_sfo: [n1(t)= rhs(sol_dfop_sfo[1]) + rhs(sol_dfop_sfo[2]), sol_dfop_sfo[3]]$
mapped_sol_dfop_sfo[1];
mapped_sol_dfop_sfo[2];

                                            - l1 t
(%o34)                      m1(t) = g n10 %e

                                               - l2 t
(%o35)                   m2(t) = (1 - g) n10 %e

                                       - l2 t           - l1 t
(%o37)           n1(t) = (1 - g) n10 %e       + g n10 %e

                                - l2 t              - l1 t
               (g - 1) l2 n10 %e         g l1 n10 %e
(%o38) n2(t) = ----------------------- - -----------------
                       l2 - k2                l1 - k2
                               2
 + ((((l1 - k2) l2 - k2 l1 + k2 ) n20 + ((l1 + (g - 1) k2) l2 - g k2 l1) n10)
   - k2 t                            2
 %e      )/((l1 - k2) l2 - k2 l1 + k2 )

## DFOP-SFO with formation fraction

In [11]:
diff_11_dfop: 'diff(m1(t), t) = - l1 * m1(t);
diff_12_dfop: 'diff(m2(t), t) = - l2 * m2(t);
diff_2_dfop_f12_sfo: 'diff(n2(t), t) = f12 * l1 * m1(t) + f12 * l2 * m2(t) - k2 * n2(t);

                            d
(%o39)                      -- (m1(t)) = - l1 m1(t)
                            dt

                            d
(%o40)                      -- (m2(t)) = - l2 m2(t)
                            dt

            d
(%o41)      -- (n2(t)) = (- k2 n2(t)) + f12 l2 m2(t) + f12 l1 m1(t)
            dt

In [12]:
atvalue(m1(t), t = 0, g * n10)$
atvalue(m2(t), t = 0, (1 - g) * n10)$
atvalue(n2(t), t = 0, n20)$
sol_dfop_f12_sfo: desolve([diff_11_dfop, diff_12_dfop, diff_2_dfop_f12_sfo], [m1(t), m2(t), n2(t)])$
sol_dfop_f12_sfo[1];
sol_dfop_f12_sfo[2];
mapped_sol_dfop_f12_sfo: [n1(t)= rhs(sol_dfop_sfo[1]) + rhs(sol_dfop_sfo[2]), sol_dfop_f12_sfo[3]]$
mapped_sol_dfop_f12_sfo[1];
mapped_sol_dfop_f12_sfo[2];

                                            - l1 t
(%o46)                      m1(t) = g n10 %e

                                               - l2 t
(%o47)                   m2(t) = (1 - g) n10 %e

                                       - l2 t           - l1 t
(%o49)           n1(t) = (1 - g) n10 %e       + g n10 %e

                                      - l2 t                  - l1 t
               (f12 g - f12) l2 n10 %e         f12 g l1 n10 %e
(%o50) n2(t) = ----------------------------- - ---------------------
                          l2 - k2                     l1 - k2
                               2
 + ((((l1 - k2) l2 - k2 l1 + k2 ) n20 + ((f12 l1 + (f12 g - f12) k2) l2
                       - k2 t                            2
 - f12 g k2 l1) n10) %e      )/((l1 - k2) l2 - k2 l1 + k2 )

## SFORB-SFO

In [13]:
m1_sforb: 'diff(m1(t), t) = - (l12 + k1) * m1(t) + l21 * m2(t);
m2_sforb: 'diff(m2(t), t) = + l12 * m1(t) - l21 * m2(t);
n2_sforb: 'diff(n2(t), t) = + k1 * m1(t) - k2 * m2(t);

                 d
(%o51)           -- (m1(t)) = l21 m2(t) + ((- l12) - k1) m1(t)
                 dt

                      d
(%o52)                -- (m2(t)) = l12 m1(t) - l21 m2(t)
                      dt

                       d
(%o53)                 -- (n2(t)) = k1 m1(t) - k2 m2(t)
                       dt

In [14]:
m1_sforb: 'diff(m1(t), t) = - l12 * m1(t) - k1 * m1(t) + l21 * m2(t);
m2_sforb: 'diff(m2(t), t) = + l12 * m1(t) - l21 * m2(t);

                 d
(%o54)           -- (m1(t)) = l21 m2(t) - l12 m1(t) - k1 m1(t)
                 dt

                      d
(%o55)                -- (m2(t)) = l12 m1(t) - l21 m2(t)
                      dt

These equations could not be handeled by desolve - it asks if an expression containing l12, l21 and k1 is positive, negative or zero and returns very complicated answers for positive or negative.

In [15]:
/* 
atvalue(m1(t), t = 0, n10)$
atvalue(m2(t), t = 0, 0)$
atvalue(n2(t), t = 0, n20)$
sol: desolve([m1_sforb, m2_sforb], [m1(t), m2(t)])$
sol[1];
sol[2];
*/

Therefore, a coefficient was set up, the Eigenvalue problem was solved, and the constants relevant for the desired initial value problem were obtained as shown below.

In [16]:
K_sforb_sfo: matrix(
[-(l12 + k1), l21, 0],
[l12, -l21, 0],
[k1, 0, -k2]);

                         [ (- l12) - k1   l21    0   ]
                         [                           ]
(%o56)                   [     l12       - l21   0   ]
                         [                           ]
                         [      k1         0    - k2 ]

In [17]:
E_sforb_sfo: eigenvectors(K_sforb_sfo)$
[[lambda, mult], vecs]: E_sforb_sfo$
lambda[1];
lambda[2];
lambda[3];

(%o59) 
               2                           2                2
       sqrt(l21  + (2 l12 - 2 k1) l21 + l12  + 2 k1 l12 + k1 ) + l21 + l12 + k1
     - ------------------------------------------------------------------------
                                          2

               2                           2                2
       sqrt(l21  + (2 l12 - 2 k1) l21 + l12  + 2 k1 l12 + k1 ) - l21 - l12 - k1
(%o60) ------------------------------------------------------------------------
                                          2

(%o61)                               - k2

In [18]:
mult;

(%o62)                             [1, 1, 1]

In [19]:
U: eigU(E_sforb_sfo);

(%o63) matrix([1, 1, 0], 
           2                           2                2
   sqrt(l21  + (2 l12 - 2 k1) l21 + l12  + 2 k1 l12 + k1 ) + l21 - l12 - k1
[- ------------------------------------------------------------------------, 
                                    2 l21
        2                           2                2
sqrt(l21  + (2 l12 - 2 k1) l21 + l12  + 2 k1 l12 + k1 ) - l21 + l12 + k1
------------------------------------------------------------------------, 0], 
                                 2 l21
               2                           2                2
[- (k1 sqrt(l21  + (2 l12 - 2 k1) l21 + l12  + 2 k1 l12 + k1 ) - k1 l21
                        2                                      2
 - k1 l12 + 2 k1 k2 - k1 )/((2 k2 - 2 k1) l21 + 2 k2 l12 - 2 k2  + 2 k1 k2), 
            2                           2                2
(k1 sqrt(l21  + (2 l12 - 2 k1) l21 + l12  + 2 k1 l12 + k1 ) + k1 l21 + k1 l12
               2                                      2
 - 2

In [20]:
c: matsolve(U, [n10, 0, 0])$
c[1];
c[2];
c[3];

                       2                             2                2
           l21 sqrt(l21  + 2 l12 l21 - 2 k1 l21 + l12  + 2 k1 l12 + k1 ) n10
(%o65) [(- -----------------------------------------------------------------)
                    2                               2                  2
               2 l21  + 4 l12 l21 - 4 k1 l21 + 2 l12  + 4 k1 l12 + 2 k1
               2                             2                2
   l12 sqrt(l21  + 2 l12 l21 - 2 k1 l21 + l12  + 2 k1 l12 + k1 ) n10
 + -----------------------------------------------------------------
            2                               2                  2
       2 l21  + 4 l12 l21 - 4 k1 l21 + 2 l12  + 4 k1 l12 + 2 k1
              2                             2                2
   k1 sqrt(l21  + 2 l12 l21 - 2 k1 l21 + l12  + 2 k1 l12 + k1 ) n10
 + ----------------------------------------------------------------
           2                               2                  2
      2 l21  + 4 l12 l21 - 4 k1 l2

                    2                             2                2
        l21 sqrt(l21  + 2 l12 l21 - 2 k1 l21 + l12  + 2 k1 l12 + k1 ) n10
(%o66) [-----------------------------------------------------------------
                 2                               2                  2
            2 l21  + 4 l12 l21 - 4 k1 l21 + 2 l12  + 4 k1 l12 + 2 k1
               2                             2                2
   l12 sqrt(l21  + 2 l12 l21 - 2 k1 l21 + l12  + 2 k1 l12 + k1 ) n10
 - -----------------------------------------------------------------
            2                               2                  2
       2 l21  + 4 l12 l21 - 4 k1 l21 + 2 l12  + 4 k1 l12 + 2 k1
              2                             2                2
   k1 sqrt(l21  + 2 l12 l21 - 2 k1 l21 + l12  + 2 k1 l12 + k1 ) n10
 - ----------------------------------------------------------------
           2                               2                  2
      2 l21  + 4 l12 l21 - 4 k1 l21 + 2 l12  + 4 k

                      k1 k2 n10
(%o67) [--------------------------------------
                                     2
        k2 l21 - k1 l21 + k2 l12 - k2  + k1 k2
                                                      k1 l21 n10
                                      - --------------------------------------]
                                                                     2
                                        k2 l21 - k1 l21 + k2 l12 - k2  + k1 k2